In [1]:
import sys
import numpy as np
import pandas as pd
import pickle
import re
import math
import os
os.environ['KMP_DUPLICATE_LIB_OK']='True'
sys.path.append(os.path.join(os.path.abspath(os.getcwd()),".."))
sys.path.append(os.path.join(os.path.abspath(os.getcwd()),"../.."))
parent_dir = os.path.abspath(os.path.join(os.getcwd(), '../..'))

In [2]:
# import MEIRL Modules
from MaxEnt_Baseline.baseline_utils import *
from MaxEnt_Baseline.Reward_Expert import *
from MaxEnt_Baseline.MaxEntBaseline import *
from utils.trajectory import Trajectory
from utils.plot_utils import *

ImportError: No module named MaxEnt_Baseline.baseline_utils

In [ ]:
# Settings for the different cases
feat_list_cases = [["laptop", "coffee", "table"],["laptop", "coffee", "table"], ["proxemics", "coffee", "table"]]
weights_cases = [[10.0, 0.0, 10.0], [10.0, 0.0, 10.0], [10.0, 0.0, 10.0]]
known_features_cases = [["table", "coffee"], ["laptop", "coffee"], ["table", "coffee"]]

traj_feat_list = [ "tablelaptop_case1", "tablelaptop_case2", "tableproxemics_case3"]
traj_idx_list = [[4, 13,0, 15], [0,1,2,3,4,5,6,7], [1,2,3,4,6]]


# TrajOpt Settings
obj_center_dict = {'HUMAN_CENTER': [-0.2, -0.5, 0.6], 'LAPTOP_CENTER': [-0.6, 0.0, 0.0]}
T = 20.0
timestep=0.5

In [3]:
# Settings for the different cases
feat_list_cases = [[]]
weights_cases = [[]]
known_features_cases = [[]]

traj_feat_list = []
traj_idx_list = [[0,1,2,3,4]]


# TrajOpt Settings
obj_center_dict = {'HUMAN_CENTER': [-0.2, -0.5, 0.6], 'LAPTOP_CENTER': [-0.6, 0.0, 0.0]}
T = 20.0
timestep=0.5

# 1. Load or Generate near-optimal expert demonstrations

In [4]:
# Setting for which Case (see paper)
case = 1

# adjust accordingly
feat_list = feat_list_cases[case-1]
weights = weights_cases[case-1]
known_features = known_features_cases[case-1]

## 1.1 Load human expert demonstrations

In [5]:
# initialize empty reward expert
Expert = GT_Reward_Expert(feat_list, weights, gen='cost',
                          starts=[], goals=[], goal_poses=None, combi=False,
                          obj_center_dict = obj_center_dict)

In [7]:
parent_dir

'/root/catkin_ws/src/FERL'

In [9]:
# CHANGED
trajectory_list = [np.load(parent_dir + '/../jaco_learning/data/pour_red{}.npy'.format(i)) for i in range(5)]

# ORIGINAL
# # load in a set of demonstrations
# data_file = parent_dir + '/data/MEIRL_demonstrations/demos_{}.p'.format(traj_feat_list[case-1])
# trajectory_list = pickle.load(open( data_file, "rb" ) )

# select subset of demonstrations & sample to fit T, timestep setting of trajopt
s_g_exp_trajs = []
for i, trajectory in enumerate(trajectory_list):
    if i not in traj_idx_list[case-1]:
        continue
    waypts = trajectory
    waypts_time = np.linspace(0.0, T, waypts.shape[0])
    traj = Trajectory(waypts, waypts_time)

    # Downsample/Upsample trajectory to fit desired timestep and T.
    num_waypts = int(T / timestep) + 1
    if num_waypts < len(traj.waypts):
        demo = traj.downsample(int(T / timestep) + 1)
    else:
        demo = traj.upsample(int(T / timestep) + 1)
    s_g_exp_trajs.append([demo.waypts])

# add to the expert
Expert.load_trajs(s_g_exp_trajs) 

## 1.2 generate near-optimal expert demonstrations

In [10]:
# extract start & goal positions from the respective demonstrations
# starts = []
# goals = []
# for trajectory in [trajectory_list[i] for i in traj_idx_list[case-1]]:
#     starts.append(trajectory[0])
#     goals.append(trajectory[-1])
    
starts = []
goals = []
for trajectory in [trajectory_list[i] for i in traj_idx_list[case-1]]:
    starts.append(trajectory[0])
    goals.append(trajectory[-1])

In [11]:
# initialize reward expert with the start & goal positions
Expert = GT_Reward_Expert(feat_list, weights, gen='cost',
                          starts=starts, goals=goals, goal_poses=None, combi=False,
                          obj_center_dict = obj_center_dict)

In [12]:
# Optional: add more random start-goal pais with a minimum distance
Expert.generate_rand_start_goal(n_trajs=0, min_dist=0.7)

In [13]:
# Step 1: generate near-optimal expert demos for all start-goal paris with TrajOpt
# Note: we found that more near optimal trajectories don't help compared to just one per pair
Expert.generate_expert_demos(n_per_s_g=1)

In [14]:
# Visualize Expert Demonstrations (Color is just z axis coordinate)
Expert.plot_trajs()

# IRL

In [15]:
NN_dict = {'n_layers': 2, 'n_units':128,
           'sin':False, 'cos':False, 'noangles':True, 'norot':False,
           'rpy':False, 'lowdim':True, 'noxyz':True, 'EErot':True,
           '6D_laptop':False, '6D_human':False, '9D_coffee':False}

IRL_dict = {'n_iters': 50,
            'n_cur_rew_traj': 1,
            'lr':1e-3, 'weight_decay':0.001, 'std':0.01}

IRL = DeepMaxEntIRL(s_g_exp_trajs=Expert.return_trajs(), goal_poses=None,
                   known_feat_list=known_features, NN_dict=NN_dict, gen='waypt',
                   obj_center_dict = obj_center_dict)

In [16]:
# Before IRL: Compare the demonstration trajectories & the current cost induced trajectories
# Colors are the randomly initialized Neural Network cost function
plot_IRL_comparison(IRL, [61,64,67], 6)
#plot_IRL_comparison(IRL, frame_idx=6)

In [17]:
plot_IRL_comparison(IRL, frame_idx=6)

In [18]:
IRL.deep_max_ent_irl(n_iters=IRL_dict['n_iters'], n_cur_rew_traj=IRL_dict['n_cur_rew_traj'],
                     lr=IRL_dict['lr'], weight_decay=IRL_dict['weight_decay'], std=IRL_dict['std'])

Iteration 49: 100%|██████████| 50/50 [01:42<00:00,  2.05s/it, avg_loss=0]      


In [19]:
# After IRL: Compare the demonstration trajectories & the current cost induced trajectories
# Colors are the learned Neural Network cost function
plot_IRL_comparison(IRL, [61,64,67], 6)

# Visualize the learned cost function in 3D 

In [20]:
# plot GT
plot_gt3D(parent_dir, Expert.env)

ValueError: All arguments should have the same length. The length of argument `color` is 1, whereas the length of  previously-processed arguments ['x', 'y', 'z'] is 7656

In [21]:
# plot learned
plot_learned3D(parent_dir, IRL.function, IRL.env)

In [32]:
def save(self):
    torch.save({
        "known_feat_list": self.known_feat_list,
        "s_g_exp_trajs": Expert.return_trajs(),
        "goal_poses": self.goal_poses,
        "NN_dict": self.NN_dict,
        "gen": self.gen,
        "cost_nn_state_dict": self.cost_nn.state_dict(),
        "max_label": self.max_label,
        "min_label": self.min_label
    }, "/root/catkin_ws/src/jaco_learning/data/pour_red_meirl.pt")

In [33]:
save(IRL)

In [26]:
'test' in 'test1'

True

In [27]:
np.zeros(1)

array([0.])

In [29]:
np.hstack((np.arange(5), 5))

array([0, 1, 2, 3, 4, 5])

In [34]:
np.arange(5)[np.arange(5) > 3]

array([4])